In [5]:
import requests
import bs4
from bs4 import BeautifulSoup
import pandas as pd
import time
from tqdm import tqdm

In [2]:
URL = "https://www.indeed.com/jobs?q=data+scientist+%2420%2C000&l=New+York&start=10"

In [3]:
r = requests.get(URL)

soup = BeautifulSoup(r.text, 'html.parser')

jobs = soup.find_all(name='div', attrs={'class':"result"})

In [4]:
def extract_company_from_result(html):
    try:
        return html.find("span",{"class":"company"}).text
    except:
        return None

In [5]:
def extract_salary_from_result(html):
    try:
        return html.find("span",{"class":"no-wrap"}).text
    except:
        return None

In [6]:
def extract_location_from_result(html):   
    try:
        return html.find("span",{'class':'location'}).text
    except:
        return None

In [7]:
def extract_job_from_result(html):
    try:
        return html.find("a").text
    except:
        return None

In [8]:
def extract_date_from_result(html):
    try:
        return html.find("span", {"class":"date"}).text
    except:
        return None

In [9]:
url_template = "https://www.indeed.com/jobs?q=data+scientist&1={}&start=10"
max_results_per_city = 2000
results = []

for city in ['New York City','Chicago','Boston', 'San Francisco Bay Area', 'Seattle']:
    for start in tqdm(range(0, max_results_per_city, 10)):
        r1 = requests.get(url_template.format(city,start))

        soup = BeautifulSoup(r1.text, 'html.parser')

        jobs = soup.find_all(name='div', attrs={'class':"result"}) # Grab the results from the request (as above)
        results.extend(jobs) # Append to the full set of results

100%|████████████████████████████████████████████████████████████████████████████████| 200/200 [01:57<00:00,  1.70it/s]


In [44]:
df = pd.DataFrame({"job_title":extract_job_from_result(result),
                   "company":extract_company_from_result(result),
                   "location":extract_location_from_result(result),
                   "salary":extract_salary_from_result(result),
                   "posted": extract_date_from_result(result),
                    "date": pd.to_datetime('today')} for result in results)

In [45]:
df.replace(to_replace="\n",value="",regex=True,inplace=True)
df.head(50)

job_title  \
0                                                       
1        Sr. Data Scientist/Machine Learning Engineer   
2                               Senior Data Scientist   
3                           Machine Learning Engineer   
4                                      Data Scientist   
5                             Sr Data Scientist, Zoro   
6                                      Data Scientist   
7            Biomedical Data Scientist/Bioinformatics   
8                         Data Scientist- Call Center   
9                       RWD Healthcare Data Scientist   
10                        Data Scientist (all levels)   
11  Freelance Data Scientist for an Award-Winning ...   
12                                     Data Scientist   
13   Data Scientist/Engineer (Open to remote Workers)   
14                          Global Big Data Scientist   
15                          Data Scientist I - Remote   
16                                     Data Scientist   
17                                     Data Scientist   
18                                     Data Scientist   
19       Sr. Data Scientist/Machine Learning Engineer   
20                                                      
21                                     Data Scientist   
22                    Machine Learning On-call Intern   
23                              Senior Data Scientist   
24                          Machine Learning Engineer   
25                            Sr Data Scientist, Zoro   
26                           Data Scientist - 64922BR   
27                      RWD Healthcare Data Scientist   
28                                     Data Scientist   
29  Data Scientist Entry Level - Pathrise Recruiti...   
30                     Junior Data Scientist | TS/SCI   
31                                     Data Scientist   
32  Internship Opportunities for Students: Data & ...   
33                                     Data Scientist   
34              Jr. Data Scientist | Development Team   
35                          Data Scientist I - Remote   
36                                     Data Scientist   
37                                     Data Scientist   
38                                     Data Scientist   
39                                                      
40       Sr. Data Scientist/Machine Learning Engineer   
41                                     Data Scientist   
42           Biomedical Data Scientist/Bioinformatics   
43                        Data Scientist- Call Center   
44                      RWD Healthcare Data Scientist   
45                        Data Scientist (all levels)   
46  Freelance Data Scientist for an Award-Winning ...   
47                                     Data Scientist   
48   Data Scientist/Engineer (Open to remote Workers)   
49                          Global Big Data Scientist   

                          company  \
0                      Triplebyte   
1                           aikiu   
2                        TRANZACT   
3                      Triplebyte   
4                  Seen by Indeed   
5                      Zoro Tools   
6                Northrop Grumman   
7                     Aspira Labs   
8                  Momentum Solar   
9                             W2O   
10               IAMUS Consulting   
11                   Mixed In Key   
12              The College Board   
13             Medidata Solutions   
14            Abbott Laboratories   
15  HMS Health Management Systems   
16      Big Data Federation, Inc.   
17             ClearOne Advantage   
18                   Metron, Inc.   
19                          aikiu   
20             ClearOne Advantage   
21               Northrop Grumman   
22                 Perspecta Labs   
23                       TRANZACT   
24                     Triplebyte   
25                     Zoro Tools   
26                          AETNA   
27                            W2O   
28          Primesys Technologies   
29                       P

In [46]:
df[['posted','etc','etc.']] = df.posted.apply(lambda x: pd.Series(str(x).split(" ")))

In [47]:
df[['posted','etc..']] = df.posted.apply(lambda x: pd.Series(str(x).split("+")))

In [48]:
df = df.drop(['etc','etc.','etc..'], axis=1)
df.head(15)

job_title              company  \
0                                                               Triplebyte   
1        Sr. Data Scientist/Machine Learning Engineer                aikiu   
2                               Senior Data Scientist             TRANZACT   
3                           Machine Learning Engineer           Triplebyte   
4                                      Data Scientist       Seen by Indeed   
5                             Sr Data Scientist, Zoro           Zoro Tools   
6                                      Data Scientist     Northrop Grumman   
7            Biomedical Data Scientist/Bioinformatics          Aspira Labs   
8                         Data Scientist- Call Center       Momentum Solar   
9                       RWD Healthcare Data Scientist                  W2O   
10                        Data Scientist (all levels)     IAMUS Consulting   
11  Freelance Data Scientist for an Award-Winning ...         Mixed In Key   
12                                     Data Scientist    The College Board   
13   Data Scientist/Engineer (Open to remote Workers)   Medidata Solutions   
14                          Global Big Data Scientist  Abbott Laboratories   

                                       location                      salary  \
0                                          None  $150,000 - $225,000 a year   
1                                          None   $70,000 - $110,000 a year   
2                                          None   $90,000 - $125,000 a year   
3                                          None  $150,000 - $250,000 a year   
4                                          None                        None   
5                                          None                        None   
6                                          None                        None   
7                            Trumbull, CT 06611                        None   
8                          South Plainfield, NJ                        None   
9                              Florham Park, NJ                        None   
10                  Linthicum Heights, MD 21090                        None   
11                                    Miami, FL                        None   
12         Reston, VA 20190 (Sunset Hills area)                        None   
13  New York, NY 10003 (Flatiron District area)                        None   
14                                United States                        None   

   posted                       date  
0      17 2020-04-20 22:36:56.544951  
1      30 2020-04-20 22:36:56.544951  
2      30 2020-04-20 22:36:56.545948  
3      17 2020-04-20 22:36:56.545948  
4      24 2020-04-20 22:36:56.546945  
5      13 2020-04-20 22:36:56.547942  
6      30 2020-04-20 22:36:56.548940  
7       4 2020-04-20 22:36:56.549936  
8       5 2020-04-20 22:36:56.549936  
9       6 2020-04-20 22:36:56.550963  
10      3 2020-04-20 22:36:56.551960  
11      8 2020-04-20 22:36:56.551960  
12      4 2020-04-20 22:36:56.553926  
13   Just 2020-04-20 22:36:56.556917  
14  Today 2020-04-20 22:36:56.558918

In [49]:
df['posted'] = df['posted'].replace(to_replace ="Just", value =0)

In [50]:
df['posted'] = df['posted'].replace(to_replace ="Today", value =0)

In [51]:
df['date'] = df['date'].dt.date

In [52]:
df = df[df.job_title != '']

In [54]:
df

job_title           company  \
1      Sr. Data Scientist/Machine Learning Engineer             aikiu   
2                             Senior Data Scientist          TRANZACT   
3                         Machine Learning Engineer        Triplebyte   
4                                    Data Scientist    Seen by Indeed   
5                           Sr Data Scientist, Zoro        Zoro Tools   
...                                             ...               ...   
18995                         Senior Data Scientist          TRANZACT   
18996                                Data Scientist  Northrop Grumman   
18997                       Sr Data Scientist, Zoro        Zoro Tools   
18998                     Machine Learning Engineer        Triplebyte   
18999               Machine Learning On-call Intern    Perspecta Labs   

      location                      salary posted        date  
1         None   $70,000 - $110,000 a year     30  2020-04-20  
2         None   $90,000 - $125,000 a year     30  2020-04-20  
3         None  $150,000 - $250,000 a year     17  2020-04-20  
4         None                        None     24  2020-04-20  
5         None                        None     13  2020-04-20  
...        ...                         ...    ...         ...  
18995     None   $90,000 - $125,000 a year     30  2020-04-20  
18996     None                        None     30  2020-04-20  
18997     None                        None     13  2020-04-20  
18998     None  $150,000 - $250,000 a year     17  2020-04-20  
18999     None                        None     30  2020-04-20  

[18008 rows x 6 columns]

In [55]:
df.to_csv('indeed_cleaned.csv')

In [19]:
csv = pd.read_csv('indeed_cleaned.csv', encoding='utf-8')
csv

Unnamed: 0                                     job_title  \
0               1  Sr. Data Scientist/Machine Learning Engineer   
1               2                         Senior Data Scientist   
2               3                     Machine Learning Engineer   
3               4                                Data Scientist   
4               5                       Sr Data Scientist, Zoro   
...           ...                                           ...   
18003       18995                         Senior Data Scientist   
18004       18996                                Data Scientist   
18005       18997                       Sr Data Scientist, Zoro   
18006       18998                     Machine Learning Engineer   
18007       18999               Machine Learning On-call Intern   

                company location                      salary  posted  \
0                 aikiu      NaN   $70,000 - $110,000 a year      30   
1              TRANZACT      NaN   $90,000 - $125,000 a year      30   
2            Triplebyte      NaN  $150,000 - $250,000 a year      17   
3        Seen by Indeed      NaN                         NaN      24   
4            Zoro Tools      NaN                         NaN      13   
...                 ...      ...                         ...     ...   
18003          TRANZACT      NaN   $90,000 - $125,000 a year      30   
18004  Northrop Grumman      NaN                         NaN      30   
18005        Zoro Tools      NaN                         NaN      13   
18006        Triplebyte      NaN  $150,000 - $250,000 a year      17   
18007    Perspecta Labs      NaN                         NaN      30   

             date  
0      2020-04-20  
1      2020-04-20  
2      2020-04-20  
3      2020-04-20  
4      2020-04-20  
...           ...  
18003  2020-04-20  
18004  2020-04-20  
18005  2020-04-20  
18006  2020-04-20  
18007  2020-04-20  

[18008 rows x 7 columns]

In [21]:
csv = csv.drop(['Unnamed: 0'], axis=1)
csv

job_title           company  \
0      Sr. Data Scientist/Machine Learning Engineer             aikiu   
1                             Senior Data Scientist          TRANZACT   
2                         Machine Learning Engineer        Triplebyte   
3                                    Data Scientist    Seen by Indeed   
4                           Sr Data Scientist, Zoro        Zoro Tools   
...                                             ...               ...   
18003                         Senior Data Scientist          TRANZACT   
18004                                Data Scientist  Northrop Grumman   
18005                       Sr Data Scientist, Zoro        Zoro Tools   
18006                     Machine Learning Engineer        Triplebyte   
18007               Machine Learning On-call Intern    Perspecta Labs   

      location                      salary  posted        date  
0          NaN   $70,000 - $110,000 a year      30  2020-04-20  
1          NaN   $90,000 - $125,000 a year      30  2020-04-20  
2          NaN  $150,000 - $250,000 a year      17  2020-04-20  
3          NaN                         NaN      24  2020-04-20  
4          NaN                         NaN      13  2020-04-20  
...        ...                         ...     ...         ...  
18003      NaN   $90,000 - $125,000 a year      30  2020-04-20  
18004      NaN                         NaN      30  2020-04-20  
18005      NaN                         NaN      13  2020-04-20  
18006      NaN  $150,000 - $250,000 a year      17  2020-04-20  
18007      NaN                         NaN      30  2020-04-20  

[18008 rows x 6 columns]

In [22]:
html = csv.to_html()

In [23]:
print(html)

<table border="1" class="dataframe">
  <thead>
    <tr style="text-align: right;">
      <th></th>
      <th>job_title</th>
      <th>company</th>
      <th>location</th>
      <th>salary</th>
      <th>posted</th>
      <th>date</th>
    </tr>
  </thead>
  <tbody>
    <tr>
      <th>0</th>
      <td>Sr. Data Scientist/Machine Learning Engineer</td>
      <td>aikiu</td>
      <td>NaN</td>
      <td>$70,000 - $110,000 a year</td>
      <td>30</td>
      <td>2020-04-20</td>
    </tr>
    <tr>
      <th>1</th>
      <td>Senior Data Scientist</td>
      <td>TRANZACT</td>
      <td>NaN</td>
      <td>$90,000 - $125,000 a year</td>
      <td>30</td>
      <td>2020-04-20</td>
    </tr>
    <tr>
      <th>2</th>
      <td>Machine Learning Engineer</td>
      <td>Triplebyte</td>
      <td>NaN</td>
      <td>$150,000 - $250,000 a year</td>
      <td>17</td>
      <td>2020-04-20</td>
    </tr>
    <tr>
      <th>3</th>
      <td>Data Scientist</td>
      <td>Seen by Indeed</td>
      <td>NaN</td>

</table>


In [24]:
import pyperclip as clip

clip.copy(f"{html}")

In [65]:
sort_by_posted = csv.sort_values('posted')

In [66]:
sort_by_posted

Unnamed: 0                                         job_title  \
1906         2009                         Global Big Data Scientist   
3114         3284  Data Scientist/Engineer (Open to remote Workers)   
2229         2350  Data Scientist/Engineer (Open to remote Workers)   
2230         2351                         Global Big Data Scientist   
3112         3282                         Global Big Data Scientist   
...           ...                                               ...   
8730         9210                             Senior Data Scientist   
8731         9211                                    Data Scientist   
8733         9213                   Machine Learning On-call Intern   
8570         9041                               Data Science Intern   
18007       18999                   Machine Learning On-call Intern   

                   company                                     location  \
1906   Abbott Laboratories                                United States   
3114    Medidata Solutions  New York, NY 10003 (Flatiron District area)   
2229    Medidata Solutions  New York, NY 10003 (Flatiron District area)   
2230   Abbott Laboratories                                United States   
3112   Abbott Laboratories                                United States   
...                    ...                                          ...   
8730              TRANZACT                                          NaN   
8731      Northrop Grumman                                          NaN   
8733        Perspecta Labs                                          NaN   
8570               Dolphin               New York, NY 10014 (SoHo area)   
18007       Perspecta Labs                                          NaN   

                          salary  posted        date  
1906                         NaN       0  2020-04-20  
3114                         NaN       0  2020-04-20  
2229                         NaN       0  2020-04-20  
2230                         NaN       0  2020-04-20  
3112                         NaN       0  2020-04-20  
...                          ...     ...         ...  
8730   $90,000 - $125,000 a year      30  2020-04-20  
8731                         NaN      30  2020-04-20  
8733                         NaN      30  2020-04-20  
8570                 $25 an hour      30  2020-04-20  
18007                        NaN      30  2020-04-20  

[18008 rows x 7 columns]

In [8]:
html.replace('\n',' ', regex=True)
html

TypeError: replace() takes no keyword arguments